# PadelTracker100: Visualize & Explore Annotations 

This notebook contains some codesnippets and helper functions for visualizing and exploring the annotations from the **PadelTracker100** dataset.

## Install Dependencies

In [ ]:
%pip install numpy==2.1.2
%pip install pandas==2.2.3
%pip install opencv-python-headless==4.10.0.84

## Helper Functions

In [2]:
from pathlib import Path
import pandas as pd
from typing import Tuple, List, Optional, Union
import datetime
import numpy.typing as npt
import json
import cv2


def coco_video_to_dataframe(
    coco_labels: str, cols_oi: Optional[List[str]] = None
) -> pd.DataFrame:
    """
    Convert COCO video labels to a Pandas DataFrame.

    Args:
        coco_labels (str): Path to the COCO JSON file containing video annotations.
        cols_oi (Optional[List[str]]): List of columns of interest to include in the DataFrame.

    Returns:
        pd.DataFrame: DataFrame containing annotations, merged with categories and images.
    """
    with open(coco_labels, "r") as f:
        labels = json.load(f)

    df_annotations = pd.DataFrame.from_records(labels["annotations"])
    df_categories = pd.DataFrame.from_records(labels["categories"]).rename(
        columns={"id": "category_id"}
    )
    df_images = pd.DataFrame.from_records(labels["images"]).rename(
        columns={"id": "image_id"}
    )

    df_annotations = df_annotations.merge(df_images, on="image_id", how="left").merge(
        df_categories, on="category_id", how="left"
    )
    if cols_oi is None:
        cols_oi = df_annotations.columns.to_list()
    df_annotations.drop(
        columns=[col for col in df_annotations.columns if col not in cols_oi],
        inplace=True,
    )
    df_annotations["frame_id"] = df_annotations["file_name"].apply(
        lambda x: int(x.split("_")[1].split(".")[0])
    )
    return df_annotations


def create_coco_pose_mask(
    frame: npt.NDArray,        
    keypoints: List[float],
    skeleton: List[Tuple[int, int]],
) -> npt.NDArray:
    """
    Create a mask with keypoints and skeleton drawn on the frame.

    Args:
        frame (npt.NDArray): Image frame on which to draw the keypoints and skeleton.
        keypoints (List[float]): List of keypoints (x, y, visibility).
        skeleton (List[Tuple[int, int]]): List of skeleton connections between keypoints.

    Returns:
        npt.NDArray: Modified frame with keypoints and skeleton overlay.
    """

    # Draw keypoints
    for i in range(0, len(keypoints), 3):
        x, y, v = keypoints[i], keypoints[i + 1], keypoints[i + 2]
        if v > 0:  # Only plot visible keypoints
            frame = cv2.circle(
                frame, (int(x), int(y)), radius=3, color=(52, 235, 171), thickness=-1
            )

    # Draw skeleton (lines between keypoints)
    for joint_start, joint_end in skeleton:
        x1, y1, v1 = (
            keypoints[joint_start * 3 - 3],
            keypoints[joint_start * 3 - 2],
            keypoints[joint_start * 3 - 1],
        )
        x2, y2, v2 = (
            keypoints[joint_end * 3 - 3],
            keypoints[joint_end * 3 - 2],
            keypoints[joint_end * 3 - 1],
        )
        if v1 > 0 and v2 > 0:  # Only draw lines between visible joints
            frame = cv2.line(
                frame,
                (int(x1), int(y1)),
                (int(x2), int(y2)),
                color=(211, 52, 235),
                thickness=2,
            )

    return frame


def inpaint_coco_pose(image: npt.NDArray, mask: npt.NDArray):
    """
    Inpaint regions in the image defined by the mask.

    Args:
        image (npt.NDArray): Input image.
        mask (npt.NDArray): Binary mask specifying regions to inpaint.

    Returns:
        npt.NDArray: Inpainted image.
    """    
    inpainted_image = cv2.inpaint(image, mask, inpaintRadius=7, flags=cv2.INPAINT_TELEA)
    return inpainted_image


def load_custom_shot_labels_dataframe(path: str) -> pd.DataFrame:
    """
    Load custom shot labels from a CSV file into a DataFrame.

    Args:
        path (str): Path to the CSV file containing shot labels.

    Returns:
        pd.DataFrame: DataFrame containing shot annotations.
    """
    df_annotations = pd.read_csv(path, sep=";", encoding="utf8")
    df_annotations["frame_id"] = df_annotations["file_name"].apply(
        lambda x: int(x.split("_")[1].split(".")[0])
    )
    return df_annotations


def add_shot_image_tag(frame: npt.NDArray, df_labels: pd.DataFrame) -> npt.NDArray:
    """
    Add a text tag to the frame indicating a shot being performed.

    Args:
        frame (npt.NDArray): Image frame.
        df_labels (pd.DataFrame): DataFrame containing shot labels.

    Returns:
        npt.NDArray: Frame with the shot tag overlay.
    """
    has_shot = df_labels["has_shot"].to_list()[0]
    if not has_shot:
        return frame

    category = df_labels["category"].to_list()[0]
    caption = f"Performing shot: {category}"
    if pd.isna(category):
        caption = "Performing a shot"

    return cv2.putText(
        frame,
        text=caption,
        org=(int((frame.shape[1] / 2)), 50),
        fontFace=cv2.FONT_HERSHEY_SIMPLEX,
        fontScale=1,
        color=(0, 255, 0),
        thickness=3,
        lineType=cv2.LINE_AA,
        bottomLeftOrigin=False,
    )


def add_bbox(frame: npt.NDArray, bbox: List[float]) -> npt.NDArray:
    """
    Draw a bounding box on the frame.

    Args:
        frame (npt.NDArray): Image frame.
        bbox (List[float]): Bounding box coordinates (x, y, width, height).

    Returns:
        npt.NDArray: Frame with the bounding box overlay.
    """
    x, y, w, h = [int(k) for k in bbox]
    return cv2.rectangle(
        frame, pt1=(x, y), pt2=(x + w, y + h), color=(0, 0, 255), thickness=2
    )


def add_ball_bbox(frame: npt.NDArray, df_labels: pd.DataFrame) -> npt.NDArray:
    """
    Add a bounding box for the ball to the frame.

    Args:
        frame (npt.NDArray): Image frame.
        df_labels (pd.DataFrame): DataFrame containing ball annotations.

    Returns:
        npt.NDArray: Frame with the ball bounding box overlay.
    """
    bbox = df_labels["bbox"].to_list()[0]    
    return add_bbox(frame, bbox)


def add_player_pose(frame: npt.NDArray, df_labels: pd.DataFrame) -> npt.NDArray:
    """
    Add player pose annotations to the frame, including bounding boxes and keypoints.

    Args:
        frame (npt.NDArray): Image frame.
        df_labels (pd.DataFrame): DataFrame containing player pose annotations.

    Returns:
        npt.NDArray: Frame with player pose overlay.
    """
    bboxs = df_labels["bbox"].to_list()
    keypoints_list = df_labels["keypoints_x"].to_list()
    num_keypoints_list = df_labels["num_keypoints"].to_list()
    skeleton_list = df_labels["skeleton"].to_list()    
    for bbox, keypoints, skeleton, num_keypoints in zip(
        bboxs, keypoints_list, skeleton_list, num_keypoints_list
    ):
        frame = add_bbox(frame, bbox)
        if num_keypoints > 0:
            frame = create_coco_pose_mask(
                frame=frame,                
                keypoints=keypoints,
                skeleton=skeleton,
            )
            # frame = inpaint_coco_pose(frame, mask)
    return frame


def add_annotations_to_frame(
    frame: npt.NDArray,
    df_shots: Optional[pd.DataFrame] = None,
    df_pose: Optional[pd.DataFrame] = None,
    df_ball: Optional[pd.DataFrame] = None,
) -> npt.NDArray:
    """
    Overlay annotations for shots, player poses, and the ball onto a frame.

    Args:
        frame (npt.NDArray): Image frame.
        df_shots (Optional[pd.DataFrame]): DataFrame containing shot annotations.
        df_pose (Optional[pd.DataFrame]): DataFrame containing player pose annotations.
        df_ball (Optional[pd.DataFrame]): DataFrame containing ball annotations.

    Returns:
        npt.NDArray: Frame with all annotations overlay.
    """
    if df_ball is not None:
        frame = add_ball_bbox(frame, df_ball)
    if df_shots is not None:
        frame = add_shot_image_tag(frame, df_shots)
    if df_pose is not None:
        frame = add_player_pose(frame, df_pose)
    return frame


def read_annotation_data(
    ball_file: str,
    player_file: str,
    shot_file: str,
    cols_oi_player: List[str],
    cols_oi_ball: List[str],
):
    """
    Load and group annotation data for ball, player, and shots.

    Args:
        ball_file (str): Path to the COCO JSON file for ball annotations.
        player_file (str): Path to the COCO JSON file for player annotations.
        shot_file (str): Path to the CSV file for shot annotations.
        cols_oi_player (List[str]): List of columns of interest for player annotations.
        cols_oi_ball (List[str]): List of columns of interest for ball annotations.

    Returns:
        Tuple[pd.DataFrame, pd.DataFrame, pd.DataFrame]: Grouped data for ball, player, and shot annotations.
    """
    df_shot = load_custom_shot_labels_dataframe(shot_file)    
    df_player = coco_video_to_dataframe(player_file, cols_oi_player)
    df_player.dropna(subset=["keypoints_x"], inplace=True)
    df_ball = coco_video_to_dataframe(ball_file, cols_oi_ball)
    df_ball.dropna(subset=["bbox"], inplace=True)
    return df_ball.groupby("frame_id"), df_player.groupby("frame_id"), df_shot.groupby("frame_id")


def annotate_video(dataset: dict, df_shot_grp, df_ball_grp, df_player_grp):
    """
    Annotate a video with shot, ball, and player pose annotations.

    Args:
        dataset (dict): Dictionary containing video information.
        df_shot_grp (pd.DataFrame): Grouped shot annotations.
        df_ball_grp (pd.DataFrame): Grouped ball annotations.
        df_player_grp (pd.DataFrame): Grouped player annotations.
    """
    video = cv2.VideoCapture(str(dataset["video"]))
    fps = video.get(cv2.CAP_PROP_FPS)    
    height = int(video.get(cv2.CAP_PROP_FRAME_HEIGHT))
    width = int(video.get(cv2.CAP_PROP_FRAME_WIDTH))
    frame_count = int(video.get(cv2.CAP_PROP_FRAME_COUNT))
    fourcc = cv2.VideoWriter_fourcc("m", "p", "4", "v")

    print(f"{frame_count=}, {height=}, {width=}")

    video_out = cv2.VideoWriter(
        filename=f"{dataset['name']}_out.mp4",
        fourcc=fourcc,
        fps=fps,
        frameSize=(width, height),
        isColor=True
    )

    frame_id = 0    
    while video.isOpened():
        ret, frame = video.read()
        if not ret:
            break
        
        try:
            df_shot_frame = df_shot_grp.get_group(frame_id)
        except KeyError:
            df_shot_frame = None

        try:
            df_ball_frame = df_ball_grp.get_group(frame_id)
        except KeyError:
            df_ball_frame = None
        
        try:
            df_player_frame = df_player_grp.get_group(frame_id)
        except KeyError:
            df_player_frame = None
        
        frame = add_annotations_to_frame(
            frame=frame,
            df_shots=df_shot_frame,
            df_ball=df_ball_frame,
            df_pose=df_player_frame
        )

        video_out.write(frame)
        frame_id += 1        

    video.release()
    video_out.release()

def get_video_stats(path: Union[str, Path]):
    """
    Retrieve statistics for a video file.

    Args:
        path (Union[str, Path]): Path to the video file.

    Returns:
        dict: Dictionary containing video name, fps, frame count, duration, and dimensions.
    """
    name = Path(path).stem
    video = cv2.VideoCapture(str(path))
    fps = video.get(cv2.CAP_PROP_FPS)    
    height = int(video.get(cv2.CAP_PROP_FRAME_HEIGHT))
    width = int(video.get(cv2.CAP_PROP_FRAME_WIDTH))
    frame_count = int(video.get(cv2.CAP_PROP_FRAME_COUNT))

    seconds = (frame_count / 30)
    length = str(datetime.timedelta(seconds=seconds))
    return {
        "name": name,
        "fps": fps,
        "frame_count": frame_count,
        "seconds": seconds,
        "length": length,
        "height": height,
        "width": width

    }    

def compute_total_frequency(df_grp, category_col: str, cnt_frames: int):
    """
    Compute the total frequency of categories over all frames.

    Args:
        df_grp (pd.DataFrame): Grouped annotation DataFrame.
        category_col (str): Column name of the category to compute frequencies for.
        cnt_frames (int): Total number of frames.

    Returns:
        pd.DataFrame: DataFrame containing category frequencies and their normalized values.
    """
    df_annotations = pd.DataFrame({"frame_id": range(cnt_frames)})
    ds_tmp = df_annotations.merge(
        df_grp.head()[[category_col, "frame_id"]], on="frame_id", how="left"
    ).drop_duplicates(subset=["frame_id", category_col])[category_col]
    df_freq = pd.merge(
        pd.DataFrame(ds_tmp.value_counts(dropna=False)).reset_index(), pd.DataFrame(ds_tmp.value_counts(dropna=False, normalize=True)).reset_index(), on=category_col
    )    
    return df_freq.sort_values(by=[category_col], ascending=True) 

def compute_average_frequency_by_frame(df_grp, cnt_col: str) -> float:        
    """
    Compute the average frequency of a column across all frames.

    Args:
        df_grp (pd.DataFrame): Grouped annotation DataFrame.
        cnt_col (str): Column name to compute the average frequency for.

    Returns:
        float: Average frequency of the column.
    """
    res= df_grp.count()[cnt_col].mean()
    return float(res)

## Constants

The code cell below assumes that the dataset was stored in parent directory `../data`. Please modify `DATA_DIR` and `LABELS_DIR` according to your project structure.

In [3]:
from pathlib import Path

DATA_DIR = Path("../data")
LABELS_DIR = Path("../data/labels")

DATASETS = [
    {
        "name": "2022_BCN_FinalF_1_sample",
        "video": DATA_DIR.joinpath("2022_BCN_FinalF_1_sample.mp4"),
        "annotations": {
            "ball": {
                "path": LABELS_DIR.joinpath("2022_BCN_FinalF_1_ball.json"),
                "format": "coco_bbox",
            },
            "player": {
                "path": LABELS_DIR.joinpath("2022_BCN_FinalF_1_pose.json"),
                "format": "coco_keypoints",
            },
            "shot": {"path": LABELS_DIR.joinpath("2022_BCN_FinalF_1_shots.csv"), "format": "custom"},
        },        
    },
    {
        "name": "2022_BCN_FinalF_1",
        "video": DATA_DIR.joinpath("2022_BCN_FinalF_1.mp4"),
        "annotations": {
            "ball": {
                "path": LABELS_DIR.joinpath("2022_BCN_FinalF_1_ball.json"),
                "format": "coco_bbox",
            },
            "player": {
                "path": LABELS_DIR.joinpath("2022_BCN_FinalF_1_pose.json"),
                "format": "coco_keypoints",
            },
            "shot": {"path": LABELS_DIR.joinpath("2022_BCN_FinalF_1_shots.csv"), "format": "custom"},
        },        
    },    
    {
        "name": "2022_BCN_FinalM_1",
        "video": DATA_DIR.joinpath("2022_BCN_FinalM_1.mp4"),
        "annotations": {
            "ball": {
                "path": LABELS_DIR.joinpath("2022_BCN_FinalM_1_ball.json"),
                "format": "coco_bbox",
            },
            "player": {
                "path": LABELS_DIR.joinpath("2022_BCN_FinalM_1_pose.json"),
                "format": "coco_keypoints",
            },
            "shot": {"path": LABELS_DIR.joinpath("2022_BCN_FinalM_1_shots.csv"), "format": "custom"},
        },
        
    },
]

COCO_BBOX_COLS_OI = [
    "id",
    "image_id",
    "category_id",
    "bbox",
    "width",
    "height",
    "file_name",
    "name",
]
COCO_KEY_POINTS_COLS_OI = [
    "id",
    "image_id",
    "category_id",
    "bbox",
    "keypoints_x",
    "keypoints_y",
    "num_keypoints",
    "skeleton",
    "width",
    "height",
    "file_name",
    "name",
]

## Save Video with Annotations

This section, reads all videos from the dataset, applies all annotations and then saves them under `./<ORIGINAL_NAME>_out.mp4`

In [8]:
for dataset in DATASETS:
    print(f"Processing {dataset['name']}")
    df_ball_grp, df_player_grp, df_shot_grp = read_annotation_data(
        ball_file=dataset["annotations"]["ball"]["path"],
        player_file=dataset["annotations"]["player"]["path"],
        shot_file=dataset["annotations"]["shot"]["path"],
        cols_oi_ball=COCO_BBOX_COLS_OI,
        cols_oi_player=COCO_KEY_POINTS_COLS_OI,
    )
    annotate_video(dataset, df_shot_grp, df_ball_grp, df_player_grp)



Processing 2022_BCN_FinalF_1_sample
frame_count=407, height=1080, width=1920
Processing 2022_BCN_FinalF_1
frame_count=45934, height=1080, width=1920
Processing 2022_BCN_FinalM_1
frame_count=53953, height=1080, width=1920


## Video Stats

This section prints out key statistics for each video in the dataset.

In [4]:
vid_stats = list()

for dataset in DATASETS[1:]:
    tmp = get_video_stats(path=dataset["video"])
    vid_stats.append(tmp)
    print(f"""VIDEO STATS FOR *{tmp["name"]}*
        {tmp['fps']=}
        {tmp['frame_count']=}        
        {tmp['length']=}
        {tmp['height']=}
        {tmp['width']=}
        """)

VIDEO STATS FOR *2022_BCN_FinalF_1*
        tmp['fps']=30.0
        tmp['frame_count']=45934        
        tmp['length']='0:25:31.133333'
        tmp['height']=1080
        tmp['width']=1920
        
VIDEO STATS FOR *2022_BCN_FinalM_1*
        tmp['fps']=30.0
        tmp['frame_count']=53953        
        tmp['length']='0:29:58.433333'
        tmp['height']=1080
        tmp['width']=1920
        


## Annotation Stats

This section prints out all key statistics about all annotations for each video in the dataset (except of the sample video).

In [12]:
from IPython.display import Markdown, display

for dataset, stats in zip(DATASETS[1:], vid_stats):    
    display(Markdown(f"### Video: {dataset['video']}") )    
    frame_count = stats["frame_count"]
    print(f"{frame_count=}")
    df_ball_grp_f, df_player_grp_f, df_shot_grp_f = read_annotation_data(
            ball_file=dataset["annotations"]["ball"]["path"],
            player_file=dataset["annotations"]["player"]["path"],
            shot_file=dataset["annotations"]["shot"]["path"],
            cols_oi_ball=COCO_BBOX_COLS_OI,
            cols_oi_player=COCO_KEY_POINTS_COLS_OI,
        )
    # Player Annotation Stats    
    df_freq = compute_total_frequency(df_player_grp_f, "name", frame_count)
    frame_freq = compute_average_frequency_by_frame(df_player_grp_f, "name")
    print(">>> Annotations: Player <<<")
    print(f"Average count per frame: {frame_freq}")
    display(df_freq )

    # Ball Annotation Stats    
    df_freq = compute_total_frequency(df_ball_grp_f, "name", frame_count)
    frame_freq = compute_average_frequency_by_frame(df_ball_grp_f, "name")
    print(">>> Annotations: Ball <<<")
    print(f"Average count per frame: {frame_freq}")
    display(df_freq )


    # Shot Type Annotation Stats
    df_freq = compute_total_frequency(df_shot_grp_f, "category", frame_count)
    frame_freq = compute_average_frequency_by_frame(df_shot_grp_f, "category")
    print(">>> Annotations: Shot-Type <<<")
    print(f"Average count per frame: {frame_freq}")
    display(df_freq )
    


### Video: ../data/2022_BCN_FinalF_1.mp4

frame_count=45934


>>> Annotations: Player <<<
Average count per frame: 4.0001741629294205


name  count  proportion
0  person  45934         1.0

>>> Annotations: Ball <<<
Average count per frame: 1.000026382439848


...

name  count  proportion
0  person  53888    0.998795
1     NaN     65    0.001205

>>> Annotations: Ball <<<
Average count per frame: 1.0034161490683229


name  count  proportion
1  Ball  19320    0.358089
0   NaN  34633    0.641911

>>> Annotations: Shot-Type <<<
Average count per frame: 1.0


category  count  proportion
1         0  14287    0.264805
2  Backhand   1649    0.030564
7  Dropshot     66    0.001223
3  Forehand   1528    0.028321
6     Other    410    0.007599
5     Serve    891    0.016514
4     Smash   1204    0.022316
0       NaN  33918    0.628658